In [77]:
import pandas as pd
import numpy as np
import os
import json
from typing import List, Dict
import re
from datetime import timedelta

In [78]:
mapping_matches = pd.read_csv("matches_mapping.csv")
mapping_players = pd.read_csv("players_mapping.csv")
mapping_teams = pd.read_csv("teams_mapping.csv")


In [79]:
mapping_matches.head()

wyscout_match_id  statsbomb_match_id
0           5464912             3892755
1           5464913             3892761
2           5464914             3892760
3           5464915             3892759
4           5464916             3892758

In [80]:
with open('physical_sample.json', 'r') as file:
    physical_data = json.load(file)
print("File data =", physical_data)

File data = [{'gameId': '5464927', 'teamId': '1625', 'teamName': 'Manchester City', 'players': [{'id': '427097', 'name': 'E. Haaland', 'metrics': [{'name': 'Count Medium Acceleration', 'values': [{'phase': 'Session', 'value': 160}, {'phase': 'Drills', 'value': 160}, {'phase': '1st Half', 'value': 91}, {'phase': '2nd Half', 'value': 69}, {'phase': "1'-15'", 'value': 27}, {'phase': "46'-60'", 'value': 17}, {'phase': "16'-30'", 'value': 36}, {'phase': "61'-75'", 'value': 22}, {'phase': "31'-45+'", 'value': 28}, {'phase': "76'-120+'", 'value': 30}]}, {'name': 'Count High Acceleration', 'values': [{'phase': 'Session', 'value': 34}, {'phase': 'Drills', 'value': 34}, {'phase': '1st Half', 'value': 18}, {'phase': '2nd Half', 'value': 16}, {'phase': "1'-15'", 'value': 6}, {'phase': "46'-60'", 'value': 8}, {'phase': "16'-30'", 'value': 8}, {'phase': "61'-75'", 'value': 2}, {'phase': "31'-45+'", 'value': 4}, {'phase': "76'-120+'", 'value': 6}]}, {'name': 'Count Medium Deceleration', 'values': [{'

In [81]:
with open('match_sample.json', 'r') as file:
    match_data = json.load(file)
print("File data =", match_data)

File data = [{'match_id': 3893117, 'match_date': '2024-05-11', 'kick_off': '17:00:00.000', 'competition': {'competition_id': 2, 'country_name': 'England', 'competition_name': 'Premier League'}, 'season': {'season_id': 281, 'season_name': '2023/2024'}, 'home_team': {'home_team_id': 40, 'home_team_name': 'West Ham United', 'home_team_gender': 'male', 'home_team_youth': False, 'home_team_group': None, 'country': {'id': 68, 'name': 'England'}, 'managers': [{'id': 86, 'name': 'David Moyes', 'nickname': None, 'dob': '1963-04-25', 'country': {'id': 201, 'name': 'Scotland'}}]}, 'away_team': {'away_team_id': 84, 'away_team_name': 'Luton Town', 'away_team_gender': 'male', 'away_team_youth': False, 'away_team_group': None, 'country': {'id': 68, 'name': 'England'}, 'managers': [{'id': 1000137, 'name': 'Robert Owen Edwards', 'nickname': 'Rob Edwards', 'dob': '1982-12-25', 'country': {'id': 249, 'name': 'Wales'}}]}, 'home_score': 3, 'away_score': 1, 'attendance': 62475, 'behind_closed_doors': False,

In [82]:
def load_all_jsons(root_folder):
    dfs = []
    
    for dirpath, _, filenames in os.walk(root_folder):
        for file in filenames:
            if file.endswith(".json"):
                file_path = os.path.join(dirpath, file)
                try:
                    with open(file_path, "r", encoding="utf-8") as f:
                        data = json.load(f)
                    
                    # Normalize (handles dicts/lists)
                    df = pd.json_normalize(data)
                    dfs.append(df)
                except Exception as e:
                    print(f"⚠️ Skipped {file_path} due to error: {e}")
    
    if dfs:
        return pd.concat(dfs, ignore_index=True)
    else:
        return pd.DataFrame()  # empty if no JSONs found



In [83]:
all_matches = load_all_jsons('.\data\matches')

In [84]:
all_matches

match_id  match_date      kick_off  home_score  away_score  attendance  \
0      3946769  2025-05-24  16:30:00.000         3.0         0.0     11523.0   
1      3946767  2025-05-24  14:15:00.000         2.0         0.0     73186.0   
2      3946766  2025-05-23  19:00:00.000         1.0         1.0     51141.0   
3      3946768  2025-05-24  19:00:00.000         1.0         1.0     19274.0   
4      3946755  2025-05-18  17:00:00.000         4.0         1.0     62269.0   
...        ...         ...           ...         ...         ...         ...   
1748   3949494  2024-08-31  16:30:00.000         0.0         2.0     15034.0   
1749   3949493  2024-08-31  19:30:00.000         2.0         3.0     29615.0   
1750   3949491  2024-08-25  18:30:00.000         0.0         2.0     29157.0   
1751   3949490  2024-08-25  16:30:00.000         2.0         3.0     30000.0   
1752   3949488  2024-08-24  19:30:00.000         2.0         0.0     81365.0   

      behind_closed_doors  neutral_ground collection_status play_status  ...  \
0                   False           False          Complete      Normal  ...   
1                   False           False          Complete      Normal  ...   
2                   False           False          Complete      Normal  ...   
3                   False           False          Complete      Normal  ...   
4                   False           False          Complete      Normal  ...   
...                   ...             ...               ...         ...  ...   
1748                False           False          Complete      Normal  ...   
1749                False           False          Complete      Normal  ...   
1750                False           False          Complete      Normal  ...   
1751                False           False          Complete      Normal  ...   
1752                False           False          Complete      Normal  ...   

     competition_stage.id competition_stage.name stadium.id  \
0                       1         Regular Season        355   
1                       1         Regular Season        353   
2                       1         Regular Season        352   
3                       1         Regular Season        348   
4                       1         Regular Season       4654   
...                   ...                    ...        ...   
1748                    1         Regular Season        552   
1749                    1         Regular Season        377   
1750                    1         Regular Season        549   
1751                    1         Regular Season       4849   
1752                    1         Regular Season        373   

                       stadium.name  stadium.country.id  stadium.country.name  \
0     Estadio Municipal de Butarque                 214                 Spain   
1         Estadio Santiago Bernabéu                 214                 Spain   
2         Estadio Benito Villamarín                 214                 Spain   
3           Estadio de Mendizorroza                 214                 Spain   
4     Estádio Cívitas Metropolitano                 214                 Spain   
...                             ...                 ...                   ...   
1748               Holstein-Stadion                  85               Germany   
1749                       BayArena                  85               Germany   
1750             Millerntor-Stadion                  85               Germany   
1751               Volkswagen Arena                  85               Germany   
1752              Signal-Iduna-Park                  85               Germany   

     referee.id                referee.name  referee.country.id  \
0          2470            César Soto Grado                 214   
1          2692          Mario Melero López                 214   
2       1002227       Víctor García Verdura                 214   
3          2402  Guillermo Cuadra Fernández                 214   
4          2559    

In [85]:
with open('event_sample.json', 'r') as file:
    event_data = json.load(file)
print("File data =", event_data)

File data = [{'id': '8f6b40bc-5df8-405c-a31e-b0a542c03819', 'index': 1, 'period': 1, 'timestamp': '00:00:00.000', 'minute': 0, 'second': 0, 'type': {'id': 35, 'name': 'Starting XI'}, 'possession': 1, 'possession_team': {'id': 34, 'name': 'Burnley'}, 'play_pattern': {'id': 1, 'name': 'Regular Play'}, 'obv_for_after': None, 'obv_for_before': None, 'obv_for_net': None, 'obv_against_after': None, 'obv_against_before': None, 'obv_against_net': None, 'obv_total_net': None, 'team': {'id': 34, 'name': 'Burnley'}, 'duration': 0.0, 'tactics': {'formation': 343, 'lineup': [{'player': {'id': 42298, 'name': 'James Trafford'}, 'position': {'id': 1, 'name': 'Goalkeeper'}, 'jersey_number': 1}, {'player': {'id': 131049, 'name': 'Ameen Al Dakhil'}, 'position': {'id': 3, 'name': 'Right Center Back'}, 'jersey_number': 28}, {'player': {'id': 18753, 'name': "Dara Joseph O'Shea"}, 'position': {'id': 4, 'name': 'Center Back'}, 'jersey_number': 2}, {'player': {'id': 12322, 'name': 'Louis Jordan Beyer'}, 'posit

In [86]:
def one_game_metric_collector(physical_data_game):
    flattened_data = []

    for game_data in physical_data_game:
        game_id = game_data['gameId']
        team_id = game_data['teamId']
        team_name = game_data['teamName']
        
        for player in game_data['players']:
            player_id = player['id']
            player_name = player['name']
            
            for metric in player['metrics']:
                metric_name = metric['name']
                
                for value_data in metric['values']:
                    phase = value_data['phase']
                    value = value_data['value']
                    
                    flattened_data.append({
                        'gameId': game_id,
                        'teamId': team_id,
                        'teamName': team_name,
                        'playerId': player_id,
                        'playerName': player_name,
                        'metricName': metric_name,
                        'phase': phase,
                        'value': value
                    })

    # Convert to DataFrame
    df = pd.DataFrame(flattened_data)

    # Pivot to get phases as columns
    pivot_df = df.pivot_table(
        index=['gameId', 'teamId', 'teamName', 'playerId', 'playerName', 'metricName'],
        columns='phase',
        values='value',
        aggfunc='first'  # Since each combination should have only one value
    ).reset_index()

    # Clean up column names
    pivot_df.columns.name = None  # Remove the 'phase' label from columns
    pivot_df.gameId = pivot_df.gameId.astype(int)
    pivot_df =pivot_df.merge(mapping_matches,  left_on = 'gameId',right_on="wyscout_match_id", how='inner').drop("wyscout_match_id",axis=1)
    return pivot_df

In [87]:
pivot_df = one_game_metric_collector(physical_data)
pivot_df.tail()

gameId teamId         teamName playerId playerName          metricName  \
331  5464927   1625  Manchester City     8277  K. Walker               M/min   
332  5464927   1625  Manchester City     8277  K. Walker           Max Speed   
333  5464927   1625  Manchester City     8277  K. Walker    Running Distance   
334  5464927   1625  Manchester City     8277  K. Walker  Sprinting Distance   
335  5464927   1625  Manchester City     8277  K. Walker      Total Distance   

          1'-15'      16'-30'     1st Half     2nd Half     31'-45+'  \
331   107.585819   115.759660   110.046297    95.508994   107.365347   
332    31.669454    30.744017    31.669454    32.403287    30.582386   
333   162.199753   207.279312   616.339355   414.594238   246.860291   
334    65.043144    67.544136   201.035324   197.388824    68.448044   
335  1613.787290  1736.394900  5304.231504  4800.918783  1954.049313   

         46'-60'      61'-75'    76'-120+'        Drills       Session  \
331    89.417102    99.361511    97.166427    102.625088    102.625088   
332    30.071753    29.980522    32.403287     32.403287     32.403287   
333   146.839859    94.124237   173.630157   1030.933594   1030.933594   
334    45.433743    64.609810    87.345268    398.424133    398.424133   
335  1341.256534  1490.422667  1969.239582  10105.150287  10105.150287   

     statsbomb_match_id  
331             3892771  
332             3892771  
333             3892771  
334             3892771  
335             3892771

In [88]:
#isolate each shot
#attach raw physical stats for each shot

In [89]:
shot_events = [event for event in event_data if event.get('type', {}).get('name') == 'Shot']

In [90]:
shot_events

[{'id': '24392d1d-314a-4063-a729-7775bc0a2c45',
  'index': 130,
  'period': 1,
  'timestamp': '00:03:04.524',
  'minute': 3,
  'second': 4,
  'type': {'id': 16, 'name': 'Shot'},
  'possession': 9,
  'possession_team': {'id': 36, 'name': 'Manchester City'},
  'play_pattern': {'id': 2, 'name': 'From Corner'},
  'obv_for_after': 0.30624077,
  'obv_for_before': 0.2782435,
  'obv_for_net': 0.027997255,
  'obv_against_after': 0.007197051,
  'obv_against_before': 0.007197051,
  'obv_against_net': 0.0,
  'obv_total_net': 0.027997255,
  'team': {'id': 36, 'name': 'Manchester City'},
  'player': {'id': 23616, 'name': 'Erling Håland'},
  'position': {'id': 23, 'name': 'Center Forward'},
  'location': [112.7, 39.9, 0.22],
  'duration': 0.471596,
  'under_pressure': True,
  'related_events': ['67dc6041-d315-4ebb-ac8e-18f3fcd24abc',
   '7d4f2f91-d6d4-4fab-bfd4-8a2eaf489d5d'],
  'shot': {'statsbomb_xg': 0.16612637,
   'shot_execution_xg': 0.3062407672,
   'shot_execution_xg_uplift': 0.1401143968,
   

In [91]:
def shots_json_to_dataframe(event_data: List[Dict]) -> pd.DataFrame:
    """
    Convert event data JSON to a flattened DataFrame.
    
    Args:
        event_data: List of event dictionaries
        
    Returns:
        pd.DataFrame: Flattened DataFrame with all event data
    """
    
    # List to store flattened events
    flattened_events = []
    
    for event in event_data:
        # Create a base dictionary with top-level fields
        flat_event = {
            'event_id': event.get('id'),
            'event_index': event.get('index'),
            'period': event.get('period'),
            'timestamp': event.get('timestamp'),
            'minute': event.get('minute'),
            'second': event.get('second'),
            'possession': event.get('possession'),
            'duration': event.get('duration'),
            'obv_for_after': event.get('obv_for_after'),
            'obv_for_before': event.get('obv_for_before'),
            'obv_for_net': event.get('obv_for_net'),
            'obv_against_after': event.get('obv_against_after'),
            'obv_against_before': event.get('obv_against_before'),
            'obv_against_net': event.get('obv_against_net'),
            'obv_total_net': event.get('obv_total_net'),
        }
        
        # Flatten nested dictionaries
        # Event type
        if event.get('type'):
            flat_event['type_id'] = event['type'].get('id')
            flat_event['type_name'] = event['type'].get('name')
        
        # Possession team
        if event.get('possession_team'):
            flat_event['possession_team_id'] = event['possession_team'].get('id')
            flat_event['possession_team_name'] = event['possession_team'].get('name')
        
        # Play pattern
        if event.get('play_pattern'):
            flat_event['play_pattern_id'] = event['play_pattern'].get('id')
            flat_event['play_pattern_name'] = event['play_pattern'].get('name')
        
        # Team
        if event.get('team'):
            flat_event['team_id'] = event['team'].get('id')
            flat_event['team_name'] = event['team'].get('name')
        
        # Location (if exists)
        if event.get('location'):
            flat_event['location_x'] = event['location'][0] if len(event['location']) > 0 else None
            flat_event['location_y'] = event['location'][1] if len(event['location']) > 1 else None
        
        # Related events (convert list to string for easier handling)
        if event.get('related_events'):
            flat_event['related_events'] = ', '.join(event['related_events'])
        
        # Tactics and lineup (handle this complex structure)
        if event.get('tactics'):
            flat_event['formation'] = event['tactics'].get('formation')
            # You might want to handle lineup separately as it's complex
        
        # Player information (if exists)
        if event.get('player'):
            flat_event['player_id'] = event['player'].get('id')
            flat_event['player_name'] = event['player'].get('name')
        
        # Position information (if exists)
        if event.get('position'):
            flat_event['position_id'] = event['position'].get('id')
            flat_event['position_name'] = event['position'].get('name')
        
        flattened_events.append(flat_event)
    
    # Convert to DataFrame
    df = pd.DataFrame(flattened_events)
    
    return df

# Usage:
#shot_events_df = shots_json_to_dataframe(shot_events)



In [92]:
def clean_numeric_column_names(df):
    """
    Change numeric column names to extract the number after the hyphen.
    
    Parameters:
    df (pandas.DataFrame): Input dataframe
    
    Returns:
    pandas.DataFrame: DataFrame with cleaned column names
    """
    result_df = df.copy()
    
    new_columns = []
    
    for col in result_df.columns:
        if '-' in col:
            # Split on hyphen and take the last part, then remove any non-digit characters
            parts = col.split('-')
            last_part = parts[-1]
            # Extract only digits from the last part
            digits = ''.join(filter(str.isdigit, last_part))
            if digits:  # Only replace if we found digits
                new_columns.append(digits)
            else:
                new_columns.append(col)
        else:
            # Keep original column name if it doesn't contain a hyphen
            new_columns.append(col)
    
    result_df.columns = new_columns
    return result_df

In [93]:
pivot_df = clean_numeric_column_names(pivot_df)
pivot_df.columns

Index(['gameId', 'teamId', 'teamName', 'playerId', 'playerName', 'metricName',
       '15', '30', '1st Half', '2nd Half', '45', '60', '75', '120', 'Drills',
       'Session', 'statsbomb_match_id'],
      dtype='object')

In [94]:
pivot_df.metricName.unique()

array(['Count HI', 'Count HSR', 'Count High Acceleration',
       'Count High Deceleration', 'Count Medium Acceleration',
       'Count Medium Deceleration', 'Count Sprint',
       'High Intensity (HI) Distance',
       'High Speed Running (HSR) Distance', 'M/min', 'Max Speed',
       'Running Distance', 'Sprinting Distance', 'Total Distance'],
      dtype=object)

for each metricName, get metric at time of shot, prorated eg 7*stat/15, also get cumulative, match so far, half so far, then date related past week, 2 weeks month

In [95]:
def add_metric_minute_values(df, minute_value, metric_col='metricName'):
    """
    Add columns with metric values for the specified minute.
    """
    result_df = df.copy()
    
    # Get numeric time period columns
    time_cols = []
    for col in result_df.columns:
        if col != metric_col and str(col).isdigit():
            time_cols.append(int(col))
    
    if not time_cols:
        return result_df
    
    time_cols_sorted = sorted(time_cols)
    
    # Find nearest higher time column
    nearest_col = next((str(tc) for tc in time_cols_sorted if tc >= minute_value), 
                      str(time_cols_sorted[-1]))
    
    print(f"For minute {minute_value}, using time period: {nearest_col}")
    
    # Add the nearest column values directly
    result_df[f'minute_value'] = (result_df[nearest_col]*minute_value)/int(nearest_col)
    
    return result_df

In [96]:
add_metric_minute_values(pivot_df,minute_value=93, metric_col='metricName')
#park this, not sure how to handle 75 to 120 minute scaling

For minute 93, using time period: 120


gameId teamId          teamName playerId playerName  \
0    5464927   1613  Newcastle United    11669  C. Wilson   
1    5464927   1613  Newcastle United    11669  C. Wilson   
2    5464927   1613  Newcastle United    11669  C. Wilson   
3    5464927   1613  Newcastle United    11669  C. Wilson   
4    5464927   1613  Newcastle United    11669  C. Wilson   
..       ...    ...               ...      ...        ...   
331  5464927   1625   Manchester City     8277  K. Walker   
332  5464927   1625   Manchester City     8277  K. Walker   
333  5464927   1625   Manchester City     8277  K. Walker   
334  5464927   1625   Manchester City     8277  K. Walker   
335  5464927   1625   Manchester City     8277  K. Walker   

                    metricName           15           30     1st Half  \
0                     Count HI          NaN          NaN          NaN   
1                    Count HSR          NaN          NaN          NaN   
2      Count High Acceleration          NaN          NaN          NaN   
3      Count High Deceleration          NaN          NaN          NaN   
4    Count Medium Acceleration          NaN          NaN          NaN   
..                         ...          ...          ...          ...   
331                      M/min   107.585819   115.759660   110.046297   
332                  Max Speed    31.669454    30.744017    31.669454   
333           Running Distance   162.199753   207.279312   616.339355   
334         Sprinting Distance    65.043144    67.544136   201.035324   
335             Total Distance  1613.787290  1736.394900  5304.231504   

        2nd Half           45           60           75          120  \
0      15.000000          NaN          NaN     2.000000    13.000000   
1      11.000000          NaN          NaN     1.000000    10.000000   
2       3.000000          NaN          NaN     0.000000     3.000000   
3      11.000000          NaN          NaN     2.000000     9.000000   
4      57.000000          NaN          NaN    13.000000    44.000000   
..           ...          ...          ...          ...          ...   
331    95.508994   107.365347    89.417102    99.361511    97.166427   
332    32.403287    30.582386    30.071753    29.980522    32.403287   
333   414.594238   246.860291   146.839859    94.124237   173.630157   
334   197.388824    68.448044    45.433743    64.609810    87.345268   
335  4800.918783  1954.049313  1341.256534  1490.422667  1969.239582   

           Drills       Session  statsbomb_match_id  minute_value  
0       15.000000     15.000000             3892771     10.075000  
1       11.000000     11.000000             3892771      7.750000  
2        3.000000      3.000000             3892771      2.325000  
3       11.000000     11.000000             3892771      6.975000  
4       57.000000     57.000000             3892771     34.100000  
..            ...           ...                 ...           ...  
331    102.625088    102.625088             3892771     75.303981  
332     32.403287     32.403287             3892771     25.112547  
333   1030.933594   1030.933594             3892771    134.563372  
334    398.424133    398.424133             3892771     67.692583  
335  10105.150287  10105.150287             3892771   1526.160676  

[336 rows x 18 columns]

need to get for each player all metrics for each date, so just the session values
then I can sub in midweek fixtures
gameid, teamid, playerid, date, metrics

In [97]:
pivot_df = pivot_df.merge(all_matches[["match_id",'match_date']], left_on = "statsbomb_match_id", right_on="match_id")

In [98]:
def shot_process_jsons(root_folder, collector_fn):
    dfs = []
    
    for dirpath, _, filenames in os.walk(root_folder):
        for file in filenames:
            if file.endswith(".json"):
                file_path = os.path.join(dirpath, file)
                try:
                    with open(file_path, "r", encoding="utf-8") as f:
                        data = json.load(f)
                    
                    # Apply your custom function
                    shot_events = [event for event in data if event.get('type', {}).get('name') == 'Shot']
                    
                    game_id = os.path.splitext(file)[0]
                    
                    # Run your function
                    df = collector_fn(shot_events)
                    
                    # Add the filename as a new column
                    df["gameId"] = game_id
                    dfs.append(df)
                except Exception as e:
                    print(f"⚠️ Skipped {file_path} due to error: {e}")
    
    if dfs:
        return pd.concat(dfs, ignore_index=True)
    else:
        return pd.DataFrame()

In [99]:
def process_jsons(root_folder, collector_fn):
    dfs = []
    
    for dirpath, _, filenames in os.walk(root_folder):
        for file in filenames:
            if file.endswith(".json"):
                file_path = os.path.join(dirpath, file)
                try:
                    with open(file_path, "r", encoding="utf-8") as f:
                        data = json.load(f)
                    
                    # Apply your custom function
                    df = collector_fn(data)
                    dfs.append(df)
                except Exception as e:
                    print(f"⚠️ Skipped {file_path} due to error: {e}")
    
    if dfs:
        return pd.concat(dfs, ignore_index=True)
    else:
        return pd.DataFrame()

In [100]:
all_physical =process_jsons('./data/physical', one_game_metric_collector)

In [101]:
all_physical.playerId = all_physical.playerId.astype(int)
all_physical.teamId = all_physical.teamId.astype(int)


In [102]:
all_physical = all_physical.merge(mapping_players, left_on='playerId',right_on='wyscout_player_id')
all_physical = all_physical.merge(mapping_teams, left_on='teamId',right_on='wyscout_team_id').drop(['teamId','playerId','gameId',"wyscout_player_id","wyscout_team_id"],axis=1).rename(columns={"statsbomb_match_id":"gameId","statsbomb_player_id":"playerId","statsbomb_team_id":"teamId"})
all_physical = all_physical.merge(all_matches[["match_id","match_date"]],left_on="gameId",right_on="match_id").drop(["match_id"],axis=1)
all_physical.head()

teamName playerName                 metricName  1'-15'  16'-30'  \
0  Manchester City     N. Aké                   Count HI     3.0      3.0   
1  Manchester City     N. Aké                  Count HSR     3.0      3.0   
2  Manchester City     N. Aké    Count High Acceleration     4.0      4.0   
3  Manchester City     N. Aké    Count High Deceleration     4.0      1.0   
4  Manchester City     N. Aké  Count Medium Acceleration    36.0     17.0   

   1st Half  2nd Half  31'-45+'  46'-60'  61'-75'  76'-120+'  Drills  Session  \
0      13.0      15.0       7.0      6.0      7.0        2.0    28.0     28.0   
1      12.0      11.0       6.0      6.0      4.0        1.0    23.0     23.0   
2      13.0       8.0       5.0      3.0      5.0        0.0    21.0     21.0   
3      10.0      12.0       5.0      6.0      5.0        1.0    22.0     22.0   
4      86.0      65.0      33.0     25.0     30.0       10.0   151.0    151.0   

    gameId  playerId  teamId  match_date  
0  3892755    3306.0    36.0  2023-08-11  
1  3892755    3306.0    36.0  2023-08-11  
2  3892755    3306.0    36.0  2023-08-11  
3  3892755    3306.0    36.0  2023-08-11  
4  3892755    3306.0    36.0  2023-08-11

In [103]:
historic_metrics = all_physical[["playerId","match_date","metricName","Session"]].groupby(["playerId","match_date","metricName"],as_index=False).first()

In [104]:
all_physical[["playerId","match_date","metricName","Session"]][all_physical["playerId"]==23616]#.groupby(["playerId","match_date","metricName"],as_index=False).first()

playerId  match_date                 metricName      Session
84       23616.0  2023-08-11                   Count HI    48.000000
85       23616.0  2023-08-11                  Count HSR    30.000000
86       23616.0  2023-08-11    Count High Acceleration    30.000000
87       23616.0  2023-08-11    Count High Deceleration    25.000000
88       23616.0  2023-08-11  Count Medium Acceleration   141.000000
...          ...         ...                        ...          ...
413765   23616.0  2025-05-25                      M/min   103.977359
413766   23616.0  2025-05-25                  Max Speed    34.283960
413767   23616.0  2025-05-25           Running Distance  1147.349976
413768   23616.0  2025-05-25         Sprinting Distance   260.331970
413769   23616.0  2025-05-25             Total Distance  8838.075485

[868 rows x 4 columns]

In [105]:
all_physical[(all_physical["playerId"]==2935 )& (all_physical["match_date"]=="2024-09-14") ]

teamName  playerName                         metricName  \
577136  Bayer Leverkusen  N. Mukiele                           Count HI   
577137  Bayer Leverkusen  N. Mukiele                          Count HSR   
577138  Bayer Leverkusen  N. Mukiele            Count High Acceleration   
577139  Bayer Leverkusen  N. Mukiele            Count High Deceleration   
577140  Bayer Leverkusen  N. Mukiele          Count Medium Acceleration   
577141  Bayer Leverkusen  N. Mukiele          Count Medium Deceleration   
577142  Bayer Leverkusen  N. Mukiele                       Count Sprint   
577143  Bayer Leverkusen  N. Mukiele       High Intensity (HI) Distance   
577144  Bayer Leverkusen  N. Mukiele  High Speed Running (HSR) Distance   
577145  Bayer Leverkusen  N. Mukiele                              M/min   
577146  Bayer Leverkusen  N. Mukiele                          Max Speed   
577147  Bayer Leverkusen  N. Mukiele                   Running Distance   
577148  Bayer Leverkusen  N. Mukiele                 Sprinting Distance   
577149  Bayer Leverkusen  N. Mukiele                     Total Distance   

        1'-15'  16'-30'  1st Half    2nd Half  31'-45+'  46'-60'  61'-75'  \
577136     NaN      NaN       NaN    3.000000       NaN      NaN      NaN   
577137     NaN      NaN       NaN    1.000000       NaN      NaN      NaN   
577138     NaN      NaN       NaN    2.000000       NaN      NaN      NaN   
577139     NaN      NaN       NaN    2.000000       NaN      NaN      NaN   
577140     NaN      NaN       NaN   19.000000       NaN      NaN      NaN   
577141     NaN      NaN       NaN   24.000000       NaN      NaN      NaN   
577142     NaN      NaN       NaN    2.000000       NaN      NaN      NaN   
577143     NaN      NaN       NaN   62.041260       NaN      NaN      NaN   
577144     NaN      NaN       NaN   23.255545       NaN      NaN      NaN   
577145     NaN      NaN       NaN   94.394044       NaN      NaN      NaN   
577146     NaN      NaN       NaN   31.553115       NaN      NaN      NaN   
577147     NaN      NaN       NaN  107.034279       NaN      NaN      NaN   
577148     NaN      NaN       NaN   38.785717       NaN      NaN      NaN   
577149     NaN      NaN       NaN  928.208102       NaN      NaN      NaN   

         76'-120+'      Drills     Session   gameId  playerId  teamId  \
577136    3.000000    3.000000    3.000000  3949506    2935.0   904.0   
577137    1.000000    1.000000    1.000000  3949506    2935.0   904.0   
577138    2.000000    2.000000    2.000000  3949506    2935.0   904.0   
577139    2.000000    2.000000    2.000000  3949506    2935.0   904.0   
577140   19.000000   19.000000   19.000000  3949506    2935.0   904.0   
577141   24.000000   24.000000   24.000000  3949506    2935.0   904.0   
577142    2.000000    2.000000    2.000000  3949506    2935.0   904.0   
577143   62.041260   62.041260   62.041260  3949506    2935.0   904.0   
577144   23.255545   23.255545   23.255545  3949506    2935.0   904.0   
577145   94.394044   94.394044   94.394044  3949506    2935.0   904.0   
577146   31.553115   31.553115   31.553115  3949506    2935.0   904.0   
577147  107.034279  107.034279  107.034279  3949506    2935.0   904.0   
577148   38.785717   38.785717   38.785717  3949506    2935.0   904.0   
577149  928.208102  928.208102  928.208102  3949506    2935.0   904.0   

        match_date  
577136  2024-09-14  
577137  2024-09-14  
577138  2024-09-14  
577139  2024-09-14  
577140  2024-09-14  
577141  2024-09-14  
577142  2024-09-14  
577143  2024-09-14  
577144  2024-09-14  
577145  2024-09-14  
577146  2024-09-14  
577147  2024-09-14  
577148  2024-09-14  
577149  2024-09-14

In [106]:
historic_metrics.head(1)

playerId  match_date metricName  Session
0    2935.0  2024-09-14   Count HI      3.0

In [107]:
all_shots=shot_process_jsons('./data/events', shots_json_to_dataframe)

In [108]:
all_matches.head(1)

match_id  match_date      kick_off  home_score  away_score  attendance  \
0   3946769  2025-05-24  16:30:00.000         3.0         0.0     11523.0   

   behind_closed_doors  neutral_ground collection_status play_status  ...  \
0                False           False          Complete      Normal  ...   

  competition_stage.id competition_stage.name stadium.id  \
0                    1         Regular Season        355   

                    stadium.name  stadium.country.id  stadium.country.name  \
0  Estadio Municipal de Butarque                 214                 Spain   

  referee.id      referee.name  referee.country.id referee.country.name  
0       2470  César Soto Grado                 214                Spain  

[1 rows x 49 columns]

In [109]:
all_shots.gameId = all_shots.gameId.astype(int)

In [110]:
all_shots = all_shots.merge(all_matches[["match_id","match_date"]],left_on="gameId",right_on="match_id").drop(["match_id"],axis=1)

In [111]:
all_shots.tail(1)

event_id  event_index  period  \
46084  f5817185-1dac-4514-8356-953d40445896       3341.0     2.0   

          timestamp  minute  second  possession  duration  obv_for_after  \
46084  00:49:20.960    94.0    20.0       181.0  0.268642       0.124349   

       obv_for_before  ...  team_name  location_x  location_y  \
46084        0.284914  ...  Brentford       116.7        46.3   

                                          related_events  player_id  \
46084  9924f520-017d-463a-8ef2-8fc4861308c3, 9af3f9a3...    10532.0   

                    player_name position_id  position_name   gameId  \
46084  Kristoffer Vassbakk Ajer         2.0     Right Back  3956010   

       match_date  
46084  2025-05-25  

[1 rows x 32 columns]

In [112]:
all_physical = clean_numeric_column_names(all_physical)
all_physical.head(1)

teamName playerName metricName   15   30  1st Half  2nd Half   45  \
0  Manchester City     N. Aké   Count HI  3.0  3.0      13.0      15.0  7.0   

    60   75  120  Drills  Session   gameId  playerId  teamId  match_date  
0  6.0  7.0  2.0    28.0     28.0  3892755    3306.0    36.0  2023-08-11

In [113]:
historic_metrics.match_date = pd.to_datetime(historic_metrics.match_date)
all_shots.match_date = pd.to_datetime(all_shots.match_date)
all_physical.match_date = pd.to_datetime(all_physical.match_date)

next steps combine table with metrics, both in game (current xyz, lagged) and historic (lagged by week, 2 week, month, cumulative) 

for every game, for every row(shot) connect: 
A) all_physical table, based on row.minute, take the nearest highest minute column (so for a shot in minute 40 take the 45 column) scale it for the time elapsed (for a shot in the 40th minute of 45 take 40/45 of each metric. if the column value is above 90 scale everything to 100, so if a shot is in the 89th minute scale it to 89/100) calculate each metricName so that there should be multiple new columns 'metricName'_now, metricName_half (the metrics so far in that half eg for an 89 min shot this will include the 120 value scaled to 89/100 and the 60 and 75 minute values), metricName_game (metric so far in the game, will be the same as metricName_half in the first half) where minutes up to 45 are the first half.
B)  for row.match_date get cumulative values for that playerId for each metricName for the previous week, 2 weeks and one month (not including this matchday) using the historic_metrics table, columns should be named 'metricName'_1_week, 'metricName'_2_week etc for each value of metricName

all of these should be added as columns to the row and the dataframe returned.

In [114]:
def process_physical_metrics(all_shots, all_physical):
    """
    Process physical metrics for each shot based on the nearest highest minute interval
    """
    results = []
    
    for idx, shot in all_shots.iterrows():
        game_id = shot['gameId']
        player_id = shot['player_id']
        minute = shot['minute']
        match_date = shot['match_date']
        
        # Filter physical data for this specific game and player
        player_physical = all_physical[
            (all_physical['gameId'] == game_id) & 
            (all_physical['playerId'] == player_id)
        ]
        
        if player_physical.empty:
            continue
            
        shot_metrics = {}
        
        # Determine which interval to use based on minute
        intervals = [15, 30, 45, 60, 75, 120]
        target_interval = min([i for i in intervals if i >= minute], default=120)
        
        # Scale factor calculation
        if target_interval ==120:
            scale_factor = minute / 100.0
        else:
            scale_factor = minute / target_interval
        
        # Process each metric
        for _, physical_row in player_physical.iterrows():
            metric_name = physical_row['metricName']
            
            # Get the metric value for the target interval
            metric_value = physical_row[str(target_interval)]
            
            # Scale the metric
            metric_now = metric_value * scale_factor if not pd.isna(metric_value) else np.nan
            
            # Calculate half metrics (first or second half)
            if minute <= 45:  # First half
                half_intervals = [15, 30, 45]
                half_metrics = [physical_row[str(i)] for i in half_intervals if i <= minute]
            else:  # Second half
                half_intervals = [45, 60, 75, 120]
                half_metrics = [physical_row[str(i)] for i in half_intervals if i <= minute]
            
            # Scale half metrics appropriately
            half_metric_scaled = 0
            for i, interval in enumerate(half_intervals):
                if interval <= minute:
                    if interval ==120:
                        interval_scale = min(minute, 100) / 100.0
                    else:
                        interval_scale = min(minute, interval) / interval
                    
                    if not pd.isna(physical_row[str(interval)]):
                        half_metric_scaled += physical_row[str(interval)] * interval_scale
            
            # Game metric (cumulative for entire game up to shot minute)
            game_intervals = [15, 30, 45, 60, 75, 120]
            game_metrics = [physical_row[str(i)] for i in game_intervals if i <= minute]
            
            game_metric_scaled = 0
            for interval in game_intervals:
                if interval <= minute:
                    if interval ==120:
                        interval_scale = min(minute, 100) / 100.0
                    else:
                        interval_scale = min(minute, interval) / interval
                    
                    if not pd.isna(physical_row[str(interval)]):
                        game_metric_scaled += physical_row[str(interval)] * interval_scale
            
            # Add to shot metrics
            shot_metrics[f'{metric_name}_now'] = metric_now
            shot_metrics[f'{metric_name}_half'] = half_metric_scaled
            shot_metrics[f'{metric_name}_game'] = game_metric_scaled
        
        # Add shot information
        shot_metrics['event_id'] = shot['event_id']
        shot_metrics['gameId'] = shot['gameId']
        shot_metrics['player_id'] = shot['player_id']
        shot_metrics['match_date'] = shot['match_date']
        shot_metrics['minute'] = shot['minute']
        
        results.append(shot_metrics)
    
    return pd.DataFrame(results)

def get_historical_metrics(all_shots, historic_metrics):
    """
    Get cumulative historical metrics for previous time periods
    """
    results = []
    
    for idx, shot in all_shots.iterrows():
        player_id = shot['player_id']
        match_date = shot['match_date']
        
        # Convert to datetime if needed
        if isinstance(match_date, str):
            match_date = pd.to_datetime(match_date)
        
        # Calculate date ranges
        one_week_ago = match_date - timedelta(days=7)
        two_weeks_ago = match_date - timedelta(days=14)
        one_month_ago = match_date - timedelta(days=30)
        
        # Filter historical metrics for this player before the match date
        player_history = historic_metrics[
            (historic_metrics['playerId'] == player_id) & 
            (historic_metrics['match_date'] < match_date)
        ]
        
        shot_historical = {}
        
        # Calculate metrics for different time periods
        time_periods = [
            ('1_week', one_week_ago),
            ('2_week', two_weeks_ago), 
            ('1_month', one_month_ago)
        ]
        
        for period_name, cutoff_date in time_periods:
            period_data = player_history[player_history['match_date'] >= cutoff_date]
            
            if not period_data.empty:
                # Group by metric and calculate cumulative values
                metric_sums = period_data.groupby('metricName')['Session'].sum()
                
                for metric_name, cumulative_value in metric_sums.items():
                    shot_historical[f'{metric_name}_{period_name}'] = cumulative_value
            else:
                # No data for this period
                for metric_name in player_history['metricName'].unique():
                    shot_historical[f'{metric_name}_{period_name}'] = np.nan
        
        # Add shot information
        shot_historical['event_id'] = shot['event_id']
        shot_historical['gameId'] = shot['gameId']
        shot_historical['player_id'] = shot['player_id']
        shot_historical['match_date'] = shot['match_date']
        
        results.append(shot_historical)
    
    return pd.DataFrame(results)

def integrate_all_data(all_shots, all_physical, historic_metrics):
    """
    Main function to integrate all data sources
    """
    # Process physical metrics
    print("Processing physical metrics...")
    physical_processed = process_physical_metrics(all_shots, all_physical)
    
    # Process historical metrics
    print("Processing historical metrics...")
    historical_processed = get_historical_metrics(all_shots, historic_metrics)
    
    # Merge all data
    print("Merging data...")
    
    # First merge physical metrics
    merged_df = all_shots.merge(
        physical_processed, 
        on=['event_id', 'gameId', 'player_id', 'match_date', 'minute'],
        how='left'
    )
    
    # Then merge historical metrics
    merged_df = merged_df.merge(
        historical_processed,
        on=['event_id', 'gameId', 'player_id', 'match_date'], 
        how='left'
    )
    
    return merged_df

# Example usage:
# Assuming your DataFrames are loaded as:
# all_shots, all_physical, historic_metrics

# Process the data
final_df = integrate_all_data(all_shots, all_physical, historic_metrics)

# Display sample of results
print(final_df.head())
print(f"Final DataFrame shape: {final_df.shape}")
print(f"New columns added: {[col for col in final_df.columns if col not in all_shots.columns]}")

Processing physical metrics...
Processing historical metrics...
Merging data...
                               event_id  event_index  period     timestamp  \
0  24392d1d-314a-4063-a729-7775bc0a2c45        130.0     1.0  00:03:04.524   
1  3c527d7b-6932-4190-8424-d1d3dcdd6a4d        191.0     1.0  00:05:11.529   
2  157da96f-2535-42f1-aaa4-273dc8ae2f12        368.0     1.0  00:10:51.930   
3  6a0404a3-2dd6-44d2-8c70-15bb2f858b82        535.0     1.0  00:14:17.334   
4  c06abd5a-b096-47eb-8352-6a5470db6d83        629.0     1.0  00:17:42.690   

   minute  second  possession  duration  obv_for_after  obv_for_before  ...  \
0     3.0     4.0         9.0  0.471596       0.306241        0.278243  ...   
1     5.0    11.0        11.0  1.023995       0.000000        0.034124  ...   
2    10.0    51.0        21.0  0.363535       0.000000        0.204285  ...   
3    14.0    17.0        27.0  1.067938       0.000000        0.095475  ...   
4    17.0    42.0        30.0  0.687717       0.047946  

In [115]:
final_df.to_csv("final_df.csv")

In [116]:
historic_metrics[historic_metrics["playerId"]==23616]

playerId match_date                 metricName      Session
378546   23616.0 2023-08-11                   Count HI    48.000000
378547   23616.0 2023-08-11                  Count HSR    30.000000
378548   23616.0 2023-08-11    Count High Acceleration    30.000000
378549   23616.0 2023-08-11    Count High Deceleration    25.000000
378550   23616.0 2023-08-11  Count Medium Acceleration   141.000000
...          ...        ...                        ...          ...
379409   23616.0 2025-05-25                      M/min   103.977359
379410   23616.0 2025-05-25                  Max Speed    34.283960
379411   23616.0 2025-05-25           Running Distance  1147.349976
379412   23616.0 2025-05-25         Sprinting Distance   260.331970
379413   23616.0 2025-05-25             Total Distance  8838.075485

[868 rows x 4 columns]

In [ ]:
def fix_special_characters(df):
    # Replace common encoding issues
    replacement_map = {
        'Ã©': 'é',
        'Ã¡': 'á',
        'Ã­': 'í',
        'Ã³': 'ó',
        'Ãº': 'ú',
        'Ã±': 'ñ',
        'Ã£': 'ã',
        'Ã¶': 'ö',
        'Ã¼': 'ü',
        'Ã§': 'ç',
        'Ã': 'À'  # and other capital letters
    }
    
    # Apply to all string columns
    for col in df.select_dtypes(include=['object']):
        df[col] = df[col].astype(str)
        for wrong, correct in replacement_map.items():
            df[col] = df[col].str.replace(wrong, correct)
    
    return df

def concatenate_cup_comps(chosen_dir):
    df_list = []
    #os.chdir("C:\\Users\\conny\\OneDrive\\Documents\\Projects\\Hudl_Performance\\Hudl_Performance_Insights_2025\")
    
    for file in [f for f in os.listdir() if f.endswith('.csv')]:
        aux = pd.read_csv(file, skiprows=1, encoding='utf-8')  # Latin-1 often works well
        df_list.append(aux)
    
    df = pd.concat(df_list, axis=0, ignore_index=True)
    df = fix_special_characters(df)
    return df

In [ ]:
cup_df = concatenate_cup_comps('.\cup_comps')
#os.chdir("C:\\Users\\conny\\OneDrive\\Documents\\Projects\\Hudl_Performance\\Hudl_Performance_Insights_2025")

In [ ]:
#os.chdir("C:\\Users\\conny\\OneDrive\\Documents\\Projects\\Hudl_Performance\\Hudl_Performance_Insights_2025")

In [200]:
def extract_players_with_team_to_dataframe(json_folder_path):
    """
    Extract player info with team_name from parent level and nickname/name fallback
    """
    players_data = []
    
    os.chdir(json_folder_path)
    
    for file in os.listdir():
        if file.endswith('.json'):
            try:
                with open(file, 'r', encoding='utf-8') as f:
                    data = json.load(f)
                
                # If data is a list, process each item
                if isinstance(data, list):
                    for item in data:
                        team_name = item.get('team_name')  # Get team_name from parent level
                        
                        if isinstance(item, dict) and 'lineup' in item:
                            lineup = item['lineup']
                            if isinstance(lineup, list):
                                for player in lineup:
                                    player_id = player.get('player_id')
                                    birth_date = player.get('birth_date')
                                    
                                    if player_id is not None and birth_date is not None:
                                        # Use nickname if available, otherwise use name
                                        player_nickname = player.get('player_nickname')
                                        player_name = player.get('player_name')
                                        display_name = player_nickname if player_nickname else player_name
                                        
                                        players_data.append({
                                            'player_id': player_id,
                                            'birth_date': birth_date,
                                            'team_name': team_name,
                                            'player_nickname': player_nickname,
                                            'player_name': player_name,
                                            'display_name': display_name,  # Combined field for convenience
                                            'source_file': file
                                        })
                
            except Exception as e:
                print(f"Error processing {file}: {e}")
                continue
    
    # Create DataFrame and remove duplicates
    if players_data:
        df = pd.DataFrame(players_data)
        df = df.drop_duplicates(subset=['player_id', 'birth_date']).reset_index(drop=True)
        return df
    else:
        return pd.DataFrame()

In [220]:
player_bio = extract_players_with_team_to_dataframe('./data/lineups')
player_bio =player_bio.drop(["player_nickname","player_name","source_file"],axis=1)

In [221]:
player_bio

player_id  birth_date        team_name               display_name
0          3067  1993-08-17  Manchester City             Ederson Moraes
1          3089  1991-06-28  Manchester City            Kevin De Bruyne
2          3193  1994-08-10  Manchester City             Bernardo Silva
3          3205  1990-05-28  Manchester City                Kyle Walker
4          3306  1995-02-18  Manchester City                 Nathan Aké
...         ...         ...              ...                        ...
2458     395797  2006-11-29      Southampton              Joachim Sanda
2459      80945  2004-03-12   Leicester City  Samuel Charles Braybrooke
2460     397195  2006-01-02  Manchester City          Claudio Echeverri
2461      47258  2003-09-19          Everton       Reece Belfield Welch
2462     406656  2006-12-12      Southampton               Jayden Moore

[2463 rows x 4 columns]

In [ ]:
#os.chdir("C:\\Users\\conny\\OneDrive\\Documents\\Projects\\Hudl_Performance\\Hudl_Performance_Insights_2025")

In [ ]:
#final_df = final_df.merge(dobs,on="player_id")

event_id  event_index  period  \
0      24392d1d-314a-4063-a729-7775bc0a2c45        130.0     1.0   
1      3c527d7b-6932-4190-8424-d1d3dcdd6a4d        191.0     1.0   
2      157da96f-2535-42f1-aaa4-273dc8ae2f12        368.0     1.0   
3      6a0404a3-2dd6-44d2-8c70-15bb2f858b82        535.0     1.0   
4      c06abd5a-b096-47eb-8352-6a5470db6d83        629.0     1.0   
...                                     ...          ...     ...   
46080  3b0ea29f-1f0b-42ce-98aa-48427ca50665       2865.0     2.0   
46081  7b53c24a-0e42-41e1-b375-aa6d19beb9c3       2942.0     2.0   
46082  319df479-728f-464c-a232-4b370425d2d2       3067.0     2.0   
46083  6034e351-b75c-4791-8f6a-4016683a44db       3290.0     2.0   
46084  f5817185-1dac-4514-8356-953d40445896       3341.0     2.0   

          timestamp  minute  second  possession  duration  obv_for_after  \
0      00:03:04.524     3.0     4.0         9.0  0.471596       0.306241   
1      00:05:11.529     5.0    11.0        11.0  1.023995       0.000000   
2      00:10:51.930    10.0    51.0        21.0  0.363535       0.000000   
3      00:14:17.334    14.0    17.0        27.0  1.067938       0.000000   
4      00:17:42.690    17.0    42.0        30.0  0.687717       0.047946   
...             ...     ...     ...         ...       ...            ...   
46080  00:33:32.691    78.0    32.0       152.0  1.414801       0.176586   
46081  00:36:43.785    81.0    43.0       159.0  0.069610       0.106102   
46082  00:40:24.271    85.0    24.0       163.0  1.248465       0.000000   
46083  00:46:40.234    91.0    40.0       174.0  1.133116       0.000000   
46084  00:49:20.960    94.0    20.0       181.0  0.268642       0.124349   

       obv_for_before  ...  Count Medium Deceleration_1_month  \
0            0.278243  ...                                NaN   
1            0.034124  ...                                NaN   
2            0.204285  ...                                NaN   
3            0.095475  ...                                NaN   
4            0.076592  ...                                NaN   
...               ...  ...                                ...   
46080        0.064824  ...                              653.0   
46081        0.101675  ...                              366.0   
46082        0.047922  ...                              123.0   
46083        0.052208  ...                              366.0   
46084        0.284914  ...                              102.0   

       Count Sprint_1_month  High Intensity (HI) Distance_1_month  \
0                       NaN                                   NaN   
1                       NaN                                   NaN   
2                       NaN                                   NaN   
3                       NaN                                   NaN   
4                       NaN                                   NaN   
...                     ...                                   ...   
46080                  57.0                           3199.729187   
46081                  48.0                           2547.164031   
46082                  12.0                            529.027877   
46083                  48.0                           2547.164031   
46084                  12.0                            659.473710   

       High Speed Running (HSR) Distance_1_month  M/min_1_month  \
0                                            NaN            NaN   
1                                            NaN            NaN   
2                                            NaN            NaN   
3                                            NaN            NaN   
4                                            NaN            NaN   
...                                          ...            ...   
46080                                2518.545654     431.739919   
46081                                1840.390290     400.288188   
46082                                 319.174274     330.714379   
46083                    